## Demonstration of ogcapi API

The initial attempt to use the `owslib` library failed due to issus in the requests getting through to the F5.

Work from here down uses `requests` directly.

In [8]:
import folium
import requests

### Get some GeoJSON data and display it directly on a `folium` map.

In [9]:
# Get the data
params = {'f': 'json', 'limit': 1000}
response = requests.get('https://ogcapi.bgs.ac.uk/collections/offshore-sample-geochemical-data/items', params=params)
data = response.json()
data

{'type': 'FeatureCollection',
 'features': [{'type': 'Feature',
   'properties': {'sample_alias': None,
    'x': -2.63833,
    'x_bng': 365855,
    'terminal_depth': 2.47,
    'sio2_per': None,
    'mn_per': 0.063,
    'ge_ppm': None,
    'cd_ppm': 0.0,
    'pb_ppm': 32.0,
    'equipment_start_date': '1986-11-15T03:30:00',
    'sample_source': 'Cruise: 1986/3',
    'y': 61.3495,
    'analysis_source': 'Concentrations of minor and major chemical elements determined in the fine fraction of superficial seabed samples collected between 1968 and 1986. Samples were analysed by Direct Reading Emission Spectrometry – E1000 1985-1988.',
    'p_per': 0.26,
    'fe2o3_per': 16.95,
    'rb_ppm': 126.0,
    'sn_ppm': None,
    'bi_ppm': 6.0,
    'activity_id': 1941393.0,
    'client': 'British Geological Survey',
    'xy_source': 'Lat/Long Converter',
    'li_ppm': 42.1,
    'k2o_per': 4.21,
    'co_ppm': 25.0,
    'sr_ppm': 199.0,
    'ba_ppm': 374.0,
    'u_ppm': None,
    'contractor': 'British 

In [10]:
# Define an initial map centred on and zoomed to the UK
m = folium.Map(location=[55, -2], zoom_start=5)

In [11]:
# Create a basic unstyled tooltip
tooltip = folium.features.GeoJsonTooltip(
    fields=['zn_ppm'],
    aliases=['Zinc ppm'])

In [12]:
# Populate and display the map
folium.GeoJson(
    data,
    tooltip=tooltip,
    marker=folium.CircleMarker()
).add_to(m)
m

### Now get the data into geopandas, transform it and then create a map

In [13]:
import geopandas as gpd
import pandas as pd
import branca.colormap as cm
from shapely.geometry import Polygon

In [17]:
# Get all the data in batches of 'limit'.
# This is a bit ugly, there may be a neater way.
sample_list = []
offset = 0
limit = 500
params = {'f': 'json', 'offset': offset, 'limit': limit}
response = requests.get('https://ogcapi.bgs.ac.uk/collections/offshore-sample-geochemical-data/items', params=params)
data = response.json()
while len(data['features']) == limit:
    # Get JSON into GeoPandas
    sample_list.append(gpd.GeoDataFrame.from_features(data['features']))
    # Get the next batch
    offset += limit
    params = {'f': 'json', 'offset': offset, 'limit': limit}
    response = requests.get('https://ogcapi.bgs.ac.uk/collections/offshore-sample-geochemical-data/items', params=params)
    data = response.json()

# Add the final batch if not empty
if len(data['features']) > 0:
    sample_list.append(gpd.GeoDataFrame.from_features(data['features']))

# Concatenate dataframes into one
samples = pd.concat(
    sample_list,
    ignore_index=True,
)
# Set geometry
samples = samples.set_geometry('geometry')
samples.tail()

geometry sample_alias                     client  \
17513  POINT (-5.83588 56.51473)         None  British Geological Survey   
17514  POINT (-3.11796 59.84818)         None  British Geological Survey   
17515  POINT (-3.11533 59.84938)         None  British Geological Survey   
17516  POINT (-6.64658 56.46540)         None  British Geological Survey   
17517  POINT (-2.02901 60.18790)         None  British Geological Survey   

        x_ed50  water_depth  mgo_per  tio2_per  zn_ppm  nb_ppm nd_ppm  ...  \
17513 -5.83417         77.0      NaN       NaN     NaN     NaN   None  ...   
17514 -3.11616         73.0     2.76      0.00     0.0    40.0   None  ...   
17515 -3.11353         75.0     3.61      0.00     0.0    21.0   None  ...   
17516 -6.64486         82.0     1.83      0.59    45.0     0.0   None  ...   
17517 -2.02722         80.0      NaN       NaN     NaN     NaN   None  ...   

      be_ppm sc_ppm  ni_ppm zr_ppm  la_ppm  \
17513    NaN   None     NaN    NaN     NaN   
17514    0.0   None    13.0   32.0    46.0   
17515    0.0   None    11.0   52.0    40.0   
17516    0.6   None    29.0  128.0    19.0   
17517    NaN   None     NaN    NaN     NaN   

                                 accessuse_restric         xy_source  b_ppm  \
17513  unrestricted use, copyright acknowledgement              None    NaN   
17514  unrestricted use, copyright acknowledgement  Main Chain Decca   27.0   
17515  unrestricted use, copyright acknowledgement  Main Chain Decca   22.0   
17516  unrestricted use, copyright acknowledgement  Main Chain Decca   80.0   
17517  unrestricted use, copyright acknowledgement  Main Chain Decca    NaN   

       cu_ppm ce_ppm  
17513     NaN   None  
17514     0.0   None  
17515     0.0   None  
17516     7.0   None  
17517     NaN   None  

[5 rows x 68 columns]

In [18]:
samples.dtypes

geometry             geometry
sample_alias           object
client                 object
x_ed50                float64
water_depth           float64
                       ...   
accessuse_restric      object
xy_source              object
b_ppm                 float64
cu_ppm                float64
ce_ppm                 object
Length: 68, dtype: object

In [19]:
# Rename, convert and select columns. Set the CRS.
samples.rename(columns={'id': 'id', 'b_ppm ': 'b_ppm '}, inplace=True)
# samples['datetime'] = pd.to_datetime(samples['datetime']) # leave as string for now
samples['id'] = samples['id'].astype(int)
samples = samples[['id', 'client', 'water_depth', 'cu_ppm ', 'geometry']]
samples.set_crs(epsg=4326, inplace=True)
samples.head()

KeyError: 'id'

In [ ]:
samples.dtypes

In [ ]:
samples.describe()